## What will I likely need to know how to do in order to produce a clean dataset?
* fill in missing values **or** remove rows with missing values
* break-up columns containing more than one chunk of data within cells into multiple columns
* remove unecessary white space from cells
* standardize data (fix typos & inconsistencies; format dates; standardize data types)
* merge duplicate rows **or** drop duplicates
* remove unnecessary data (drop extraneous variables or observations)
* check for data discrepancies

These are general actions, that for the most part can be done in any order. You may even find yourself repeating certain actions along the way as you clean and assess your data. Becoming familiar with your data beforehand can help you map out a data cleaning plan.

Two useful libraries we will want to import are **pandas** and **numpy**. A nice feature of Pandas is the built-in dataframe object type which is built for dealing with tabular data. NumPy contains many functions available for working with numerical data. Another useful library that may come in handy is **re** for creating and matching regular expressions. Each of these libraries has a whole host of potentially useful features beyond what we can cover in a short workshop, so be sure to check the documentation for each if you're looking to do something specific!

Pandas docs: https://pandas.pydata.org/docs/

NumPy docs: https://numpy.org/doc/

Re docs: https://docs.python.org/3/library/re.html  
(note, the Python doc mentions an additional 3rd party regular expression library which offers additional functionality: regex)


For this workshop we will be using a sample dataset that contains data on audiobooks from Audible. Let us first load it into our notebook as a pandas dataframe and see how the data is structured.

What we want to do with the data will guide what steps we need to take to clean it. Maybe we want to do statistical analysis relating to the ratings on the audiobooks, or find the distribution of ratings for each author and narrator.

In [1]:
# import our libraries
import pandas as pd
import numpy as np
import re

# read our tabular data into a dataframe and then show the first 5 rows:



We can already see some issues in how our data is structured.
(aside: the output of certain Python functions may be slightly different depending on which version you have installed)

Additionally, we can use the .info() and .describe() dataframe functions to get a better sense of our data.

In [2]:
# .info() and .describe()




We should see several issues that need to be addressed before our data is considered clean and note some steps needed to get it ready for analysis (assuming that our analysis requires all the columns):

- remove any entries from the star column that are 'not rated yet'
- limit our data to only audiobooks longer than 10 minutes (arbitrary, but we want to exclude anything that's likely just a preview)
- remove 'Writtenby:' and 'Narratedby:' from the author and narrator columns
- convert and standardize the time column to something numerical to allow comparison between values
- separate the multiple data values in the 'stars' column into their own columns
- the releasedate column appears to be in DD-MM-YY format, let's put it instead into YYYY-MM-DD so that we're able to order it chronologically


And a couple other things to note, but we won't do anything to 'fix' them here:

- will likely want to separate the first and last names for authors and narrators
- its not clear what the price column units should be. Is it in USD?


## fill in missing values:

Now that we have our tabular data in a dataframe, we can start the process of cleaning the data. The first thing we will do here is deal with missing values. What do we mean by missing values? Cells where data either hasn't been entered or is marked as 'not available' in some way or another.

If we want to look for how many missing values our data has in the form of blank cells we can use the .isnull() method to check for null values and the .sum() function to see how many there are in each column:


In [3]:
# .isnull()


In [4]:
# .isnull().sum()


We see that for our data there are no blank cells anywhere. Though data you encounter in the future may, so I'll introduce a couple of methods that are useful for dealing with that. Maybe you want to fill in all missing values with zeros or with the string 'NA', in that case we can use the .fillna method:

    my_dataframe.fillna('NA', inplace=True)

Or perhaps we want to get rid of those observations entirely (i.e. rows). For missing data in the form of blank cells, we can simply use panda's dataframes .dropna() function:

    my_dataframe.dropna(inplace=True)

In both commands above, setting the paramter 'inplace = True' modifies the dataframe directly instead of outputting a new dataframe object.

Let's see what this does to a small test dataframe:


In [5]:
# read in 'missing.csv'


In [5]:
# .fillna(0)


In [6]:
# .dropna()


However, for the data we are working with the 'missing values' are where the item has not yet been rated and in our case that's signified by the string 'Not rated yet', so we must find a different way to replace or remove these values. If we wanted to replace those values (or any other values) with something else, we could use another built-in pandas function:

    my_dataframe.replace('thing to replace','thing replacing it')

Actually, this function gives us a way to remove those rows using the other functions we just encountered. We could replace the values with NA values and then drop them! Let's see how that works on our test dataframe where we previously filled the NA's with 0's:

In [7]:
#replace 0s and drop NAs


I'll also show an alternative way to get a dataframe without those rows by using the value we want to omit, just for some extra Pandas practice.

Remember we can call a column from our dataframe by its header label, which will return a pandas Series. For example, calling 

    df1['stars']

would return the stars column values as a series. Combining that with a conditional statement turns it into a Boolean series of True/False entries 

    df1['stars'] != 'Not rated yet'

Which we can use to get a subset of our dataframe by putting it all inside the square brackets of our dataframe variable:

    df1[df1['stars'] != 'Not rated yet']

In [8]:
# get subset where items have a rating (remember to put it into a new variable!)


#Then let's use describe() to see how our dataframe has changed


We see that we have way fewer rows now, and now our most frequent stars value is '5 out of 5 stars1 rating'

### Value Imputation

In some cases of having numerical data, instead of dropping observations with missing values we may want to impute or insert a reasonable guess of sorts through one of various methods. There are many options for imputing values. They vary in difficulty, with the best method to use depending on details of your data and of the missing values. The simplest methods replace missing values with one of either the mean or mode of the known variable values, which is an ok method to use if there are only a few missing values in your dataset. Other methods are more involved and use interpolation or other algorithms to estimate a value. We will not cover them here, but I link some resources to look through for the interested reader:

Interpolation methods using pandas and the scipy library:
https://pandas.pydata.org/docs/user_guide/missing_data.html#interpolation

Link containing general info on when to use different imputation techniques:
https://medium.com/@tarangds/a-comprehensive-guide-to-data-imputation-techniques-strategies-and-best-practices-152a10fee543

## remove unecessary white space

We want to make sure there is no leading or trailing whitespace in our data as this can skew interpretation and results. E.g. 'bananas' is treated as different than ' bananas ' even though we know they should be an equivalent data value. This is more often an issue in data that was input manually.

To remove whitespace from both ends of string values throughout our dataframe (excluding column headers) we can use the .strip() method for strings .str and cycle through our columns using:

    for item in sequence:
        # do some stuff with each item

So to edit each column in our dataframe this would look like:

    for column in df:
        df[column] = df[column].str.strip()

Note that the .strip() method removes space, tab, and newline whitespace.

Let's also make sure our headers don't contain any unnecessary whitespace using .str.strip() with pandas .columns method to get a list of just the column headers.

In [9]:
#remove trailing/leading whitespace from data


In [10]:
#remove trailing/leading whitespace from column headers


## remove unnecessary data 
Remove parts from cells containing chunks of information & drop extraneous variables or observations

In our data, we saw that our 'author' column has 'Writtenby:' in each cell before listing the authors, which is clearly unnecessary. Similarly, the 'narrator' column has 'Narratedby:' in each cell before listing the narrator. To leave only the authors and narrator in those columns we use the .str.replace() method and replace the text we don't want in our cells with an empty string, '', and with the option '*case=False*' to have it ignore the case of the text it comes across, just in case it varies across our dataframe:

    df['author'] = df['author'].str.replace('Writtenby:', '', case=False)
    df['narrator'] = df['narrator'].str.replace('Narratedby:', '', case=False)



In [11]:
# replace 'Writtenby:' and 'Narratedby:' with an empty string

# call head() again to view changes


If our dataset contains variables we know we won't need for the analysis we plan to do then we can just drop them from our dataframe with:

    df.drop(columns=['column name'], inplace=True)

Let's assume we won't be needing the 'language' column and drop it from our dataset.

In [13]:
#drop the 'language' column:


## Break-up columns containing more than one chunk of data within cells into multiple columns

### Regular expressions

Before going into this and the next step, we're going to take a little detour and learn about regular expressions. Regular expressions, or RegEx for short, are a flexible and powerful tool for doing any kind of string matching operations because they allow you to specify search patterns at a general level. As an example, in words, "I'm looking for any cells that match the format: exactly 5 alphabetical characters at the beginning, of any case, and followed by at least 1 number". In regular expression format this search string would look like:

    r"(^[a-zA-Z]{5}\d+)"

with the small 'r' out in front signaling to Python that what's closed in quotations after it is a 'raw string'. The biggest difference between a string and a raw string is that in a raw string a backslash \ is just a backslash and isn't treated as an escape character. Check out the following links to learn more: 
- https://www.w3schools.com/python/python_regex.asp
- https://docs.python.org/3/library/re.html

In [14]:
my_string = 'aAbbc51wfwefw'
my_string2 = '55abcde123sdjkl'
# search the two strings using a regex


With the following bit of code we will take the author column and split it at any comma we come across, add a prefix of 'author' to each of those new column headers, and then concatenate the new columns to the rest of the non-author columns:

    data2 = pd.concat( [data['name'],   
                        data['author'].str.split(',', expand = True).add_prefix('author'),  
                        data.loc[:,'narrator':'price']],   
                        axis = 1)


Additionally, we want to separate the stars column:


    df['avg rating (out of 5)'] = df['stars'].str.extract(r'(\d+\.\d+|\d+) out of 5 stars')
    df['number of ratings'] = df['stars'].str.extract(r'(\d+) ratings')

Convert the 'average_rating' column to numeric format (the errors='coerce' option that we see forces anything that can't be changed to numeric format to instead be replaced with a NaN value):

    df['avg rating (out of 5)'] = pd.to_numeric(df['avg rating (out of 5)'], errors='coerce')

Convert the 'num_ratings' column to numeric format

    df['number of ratings'] = pd.to_numeric(df['number of ratings'], errors='coerce')

And drop the original 'stars' column now that we've made new columns for the values within it.

    df.drop(columns=['stars'],inplace=True)



In [15]:
# split the author column

# use .head() to view changes


In [16]:
# split the stars column


# use .head() to view changes


And finally, we would likely want to separate the author and narrator columns into first and last name columns. The process would be similar to how we split the multiple authors into their own columns, except we would need to use a RegEx. For author names of the form FirstnameLastname, perhaps something like the following would work:

    r'([A-Z]{1}[a-z]+)'

However, taking another look at our data we see that the author names are not in any standard format (abbreviations, middle name included in some, names like 'McAllister', user names as author names,...), so this process would be quite a bit more involved. I leave that as an exercise for the reader, if you feel up to the challenge.

## Standardize Your Data:
### Fix typos & inconsistencies, format dates or other values, convert values, standardize data types & case

Just like the previous step, this step too can be possibly very many smaller steps depending on your data.


#### Convert the time column into something usable for comparison:

Define a function to convert time to minutes.:

    def convert_to_minutes(time_str):  
        if 'hr' in time_str and 'min' in time_str:  
            hours, mins = map(int, re.findall(r'\d+', time_str))
            return hours * 60 + mins  
        elif 'hr' in time_str:    
            hours = int(re.search(r'\d+', time_str).group())  
            return hours * 60  
        elif 'min' in time_str:    
            mins = int(re.search(r'\d+', time_str).group())  
            return mins  
        else:  
            return None
Notice our function takes care of each possible case (hours and minutes, only hours, only minutes, anything else). And once defined, we apply the conversion function to the 'time' column:

    df['time'] = df['time'].apply(convert_to_minutes)


#### Converting the 'releasedate' column into YYYY-MM-DD datetime format:

    df['releasedate']=df['releasedate'].astype('datetime64[ns]')

*read more about datetime64 data type here: https://numpy.org/devdocs/reference/arrays.datetime.html

In [17]:
# define conversion function


# Apply the conversion function to the 'time' column:


#convert values to integer type
#df_audible['time'] = pd.to_numeric(df_audible['time'], errors='coerce')

#rename the 'time' column to 'time (minutes)'


In [18]:
# convert 'releasedate' column into a standard YYYY-MM-DD format:


## merge or drop duplicate rows

You might notice your data has two separate rows for the same observation with perhaps partially filled in data in each row that complements what's in the other row. In this case we may want to merge the two rows so we have a single row for that observation and complete data for it as well.

(will probably have to do it by writing a method that compares rows. Fairly straightforward if your data has a key header, e.g. your data is on physical attributes of plants and each plant is assigned a unique ID)

Or you may find that some observations really were completely duplicated in which case we should drop duplicates:
If we want to check for duplicate rows we can use: 

    df.duplicated().sum()

And to then drop the duplicates we would use:

    df.drop_duplicates(inplace=True)


In [19]:
# check for duplicates


## Check for data discrepancies

Look for numerical outliers and remove any that are clearly errors, e.g. if one of our release date entries claimed to be from the 1800s or if we had a dataset that included a column for mouse weights and one of these read 5 lbs. For very small data sets this can be done visually with a quick sort of the data in a column. For larger datasets we will want to use statistical means to identify outliers. Unfortunately, that could be its own tutorial and we will not cover it here, though below are a couple of resources to look through to get you started:

- https://stackoverflow.com/questions/23199796/detect-and-exclude-outliers-in-a-pandas-dataframe
- https://machinelearningmastery.com/how-to-use-statistics-to-identify-outliers-in-data/







In [20]:
# sort the values of the releasedate column using .sort_values()


# Finally, save your dataframe into a file!

Saving as a .csv is preferable for data we plan to do analysis on because it's a plain text format, so WYSIWYG. Whereas if we saved instead to an Excel file it might attempt to re-format some of our data, for example our datetime data, and can introduce errors this way. To save to a .csv file we use:
    
    df.to_csv('filename.csv', encoding = 'utf-8', index = False)

Set encoding to 'utf-8' (a standard encoding), and index to 'False' so that it leaves the index out of the save file.

In [21]:
# save to a file


As happens often in coding, there are many ways to do the same thing. And also many more things we could potentially do or could have dealt with in our data, e.g replacing missing values in a column of numerical values with a reasonable assumption using a pandas function if it were reasonable for our data. Google questions and check documentation! There's a chance someone has had a similar question or their might be a specific function that's useful for doing what you want! 

I linked some useful docs in the beginning. Here are a few more useful resources that you can use or might encounter along the way:

w3schools: https://www.w3schools.com/python/default.asp

stackoverflow: https://stackoverflow.com/questions/tagged/python


### References:  

I modified information found in the following pages to create this workshop:   
https://www.kaggle.com/code/darshan77879/audible-data-magic-cleaning-assessing-enhancing#Data-Assessing-(Manual)  
https://www.kaggle.com/code/cshefali/some-common-how-tos-of-data-cleaning-in-python#6.-How-to-find-total-number-of-NA-in-each-column?